# 1.1 파이썬 래퍼 XGBoost

## 기본세팅

In [1]:
import numpy as np
import pandas as pd

import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns

import warnings

In [2]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

mpl.rc('font', family='NanumGothic') # 폰트 설정
mpl.rc('axes', unicode_minus=False) # 유니코드에서 음수 부호 설정

# 차트 스타일 설정
sns.set(font="NanumGothic", rc={"axes.unicode_minus":False}, style='darkgrid')
plt.rc("figure", figsize=(10,8))

warnings.filterwarnings("ignore")

In [3]:
#!pip install graphviz
import pandas as pd
import numpy as np
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import matplotlib.pyplot as plt
from xgboost import plot_importance, to_graphviz
import graphviz
from sklearn.metrics import accuracy_score, precision_score, recall_score, confusion_matrix, f1_score, roc_auc_score

In [4]:
# CSV 파일 경로
file_path = 'combined_training.csv'

# CSV 파일을 데이터프레임으로 읽기
data_df = pd.read_csv(file_path)

# 데이터프레임 확인
print(data_df.head())

# 'site'와 'sid' 열 제거
data_df = data_df.drop(columns=['site', 'sid'])

# 피처와 레이블 분리 (여기서는 'target' 열을 레이블로 가정)
X_features = data_df.drop(columns='leaktype')
y_label = data_df['leaktype']

# 레이블 인코딩 (문자열을 숫자로 변환)
label_encoder = LabelEncoder()
y_label_encoded = label_encoder.fit_transform(y_label)

           site                 sid     ldate  lrate  llevel leaktype  0HZ  \
0  S-4687025030  S-0359369085120315  20200708     90     256      out    0   
1  S-4677025028  S-0359369083968368  20190601     90     542      out    0   
2  S-4673025027  S-0359369085133797  20201028     90     705      out    0   
3  S-4772025022  S-0359369084117593  20200505     90     499      out    0   
4  S-4729010102  S-0359369084010178  20200520     90     423      out    0   

   10HZ  20HZ  30HZ  ...  MAX10  MAX11  MAX12  MAX13  MAX14  MAX15  MAX16  \
0    18    19    16  ...   4690    243   4710    284   4700    324   4670   
1     4     2     4  ...    310    423    300    711    270    412    270   
2     0     0     3  ...    240    751    240    897    240    741    240   
3     2     2     2  ...    370    549    360    427    370    800    370   
4     3     3     3  ...    400    521    400    395    400    461    400   

   MAX17  MAX18  MAX19  
0    230   4710    260  
1    531    290   

In [5]:
# 데이터 분포 확인
print("클래스 이름:", label_encoder.classes_)
print("타겟 값 분포:\n", pd.Series(y_label).value_counts())

클래스 이름: ['in' 'noise' 'normal' 'other' 'out']
타겟 값 분포:
 normal    19704
out       17539
in        13273
other      7019
noise      5029
Name: leaktype, dtype: int64


In [6]:
# 학습 데이터와 테스트 데이터로 분할
X_train, X_test, y_train, y_test = train_test_split(X_features, y_label_encoded, test_size=0.2, random_state=156)

# DMatrix 객체 생성
dtrain = xgb.DMatrix(data=X_train, label=y_train)
dtest = xgb.DMatrix(data=X_test, label=y_test)

## 하이퍼파라미터 설정 

In [7]:
# 하이퍼파라미터 설정
params = {
    'base_score': 0.5, 
    'booster': 'gbtree', 
    'colsample_bylevel': 1,
    'colsample_bynode': 1, 
    'colsample_bytree': 1, 
    'eval_metric': 'mlogloss',
    'gamma': 0, 
    'importance_type': 'gain',
    'interaction_constraints': '', 
    'learning_rate': 0.5, 
    'max_delta_step': 0,
    'max_depth': 6, 
    'min_child_weight': 1,
    'monotone_constraints': '()', 
    'n_estimators': 100, 
    'n_jobs': 0,
    'num_class': 5, 
    'num_parallel_tree': 1, 
    'objective': 'multi:softprob',
    'random_state': 42, 
    'reg_alpha': 0, 
    'reg_lambda': 1, 
    'scale_pos_weight': None,
    'seed': 42, 
    'subsample': 1, 
    'tree_method': 'exact', 
    'validate_parameters': 1,
    'verbosity': None
}

num_rounds = 400  # 부스팅 반복 횟수

In [8]:
# 평가 목록
wlist = [(dtrain, "train"), (dtest, "eval")]

# 모델 학습
xgb_model = xgb.train(params=params, dtrain=dtrain, num_boost_round=num_rounds, evals=wlist)


[0]	train-mlogloss:1.08879	eval-mlogloss:1.09118
[1]	train-mlogloss:0.90153	eval-mlogloss:0.90889
[2]	train-mlogloss:0.78411	eval-mlogloss:0.79635
[3]	train-mlogloss:0.71242	eval-mlogloss:0.72793
[4]	train-mlogloss:0.66061	eval-mlogloss:0.67939
[5]	train-mlogloss:0.62578	eval-mlogloss:0.64787
[6]	train-mlogloss:0.59837	eval-mlogloss:0.62405
[7]	train-mlogloss:0.57595	eval-mlogloss:0.60342
[8]	train-mlogloss:0.55814	eval-mlogloss:0.58750
[9]	train-mlogloss:0.53921	eval-mlogloss:0.57201
[10]	train-mlogloss:0.51787	eval-mlogloss:0.55289
[11]	train-mlogloss:0.49850	eval-mlogloss:0.53620
[12]	train-mlogloss:0.47563	eval-mlogloss:0.51721
[13]	train-mlogloss:0.46385	eval-mlogloss:0.50756
[14]	train-mlogloss:0.45352	eval-mlogloss:0.49891
[15]	train-mlogloss:0.43770	eval-mlogloss:0.48600
[16]	train-mlogloss:0.42584	eval-mlogloss:0.47551
[17]	train-mlogloss:0.41087	eval-mlogloss:0.46260
[18]	train-mlogloss:0.39643	eval-mlogloss:0.45097
[19]	train-mlogloss:0.38714	eval-mlogloss:0.44308
[20]	train

## XGB 예측

In [9]:
# 예측 확률
pred_probs = xgb_model.predict(dtest)
print("predict() 수행 결과값 10개만 표시")
print(np.round(pred_probs[:10], 3))

# 예측 분류
preds = np.argmax(pred_probs, axis=1)
print("예측 분류 10개만 표시")
print(f"{preds[:10]}")

predict() 수행 결과값 10개만 표시
[[0.    0.    1.    0.    0.   ]
 [0.006 0.002 0.    0.99  0.001]
 [0.001 0.    0.    0.    0.998]
 [0.    0.    1.    0.    0.   ]
 [0.    0.    1.    0.    0.   ]
 [0.003 0.    0.    0.001 0.997]
 [0.029 0.145 0.    0.    0.826]
 [0.999 0.    0.    0.    0.001]
 [0.001 0.005 0.    0.    0.993]
 [0.007 0.    0.    0.992 0.001]]
예측 분류 10개만 표시
[2 3 4 2 2 4 4 0 4 3]


## XGB 평가

In [10]:
# 성능 평가 함수
def get_clf_eval(y_test, pred=None, pred_proba=None):
    confusion = confusion_matrix(y_test, pred)
    accuracy = accuracy_score(y_test, pred)
    precision = precision_score(y_test, pred, average='weighted')
    recall = recall_score(y_test, pred, average='weighted')
    f1 = f1_score(y_test, pred, average='weighted')
    auc = roc_auc_score(y_test, pred_proba, multi_class='ovr')
   
    print("오차 행렬")
    print(confusion)
    print(f"정확도: {accuracy:.4f}, 정밀도: {precision:.4f}, 재현율: {recall:.4f}, F1: {f1:.4f}, AUC: {auc:.4f}")

In [11]:
get_clf_eval(y_test, pred=preds, pred_proba=pred_probs)

오차 행렬
[[2437   22    0   19   90]
 [  51  897    0   20   48]
 [   0    0 4023    0    0]
 [  46   15    0 1280   63]
 [  59    8    0   31 3404]]
정확도: 0.9623, 정밀도: 0.9624, 재현율: 0.9623, F1: 0.9621, AUC: 0.9967


## XGB 피처별 중요도

In [17]:
import warnings

def set_font():
    try:
        plt.rcParams['font.family'] = 'NanumGothic'
    except:
        plt.rcParams['font.family'] = 'sans-serif'
        plt.rcParams['font.sans-serif'] = ['Arial']  # 기본 폰트를 설정합니다.

# 폰트 관련 경고 메시지 무시
warnings.filterwarnings("ignore", category=UserWarning, module="matplotlib")

set_font()

In [19]:
# 폰트를 Arial로 설정
plt.rcParams['font.family'] = 'Arial'

## Feature importance 높은 순으로 feature 30개당 그래프 그리기
import matplotlib.pyplot as plt

# 피처 중요도 추출
importance = xgb_model.get_score(importance_type='weight')
sorted_importance = sorted(importance.items(), key=lambda x: x[1], reverse=True)
feature_names = [x[0] for x in sorted_importance]
importance_values = [x[1] for x in sorted_importance]

# 중요도를 가지고 있는 데이터프레임 생성
feature_importance_df = pd.DataFrame({
    'Feature': feature_names,
    'Importance': importance_values
})

# 중요도 순으로 정렬
feature_importance_df = feature_importance_df.sort_values(by='Importance', ascending=False)

# 피처를 30개씩 나누어 그래프 생성
num_features = len(feature_importance_df)
num_subplots = (num_features // 30) + 1

plt.figure(figsize=(12, 8*num_subplots))

for i in range(num_subplots):
    start_idx = i * 30
    end_idx = min((i + 1) * 30, num_features)
    
    subset_df = feature_importance_df.iloc[start_idx:end_idx]
    subset_df = subset_df.sort_values(by='Importance', ascending=True)  # 중요도가 높은 순으로 정렬
    
    plt.subplot(num_subplots, 1, i+1)
    bars = plt.barh(subset_df['Feature'], subset_df['Importance'], align='center')
    
    for bar, importance in zip(bars, subset_df['Importance']):
        plt.text(bar.get_width() + 0.005, bar.get_y() + bar.get_height()/2, f'{importance:.4f}', 
                 va='center', ha='left', fontsize=10, color='black')

    plt.xlabel('Importance')
    plt.ylabel('Feature')
    plt.title(f'Feature Importance (Top {start_idx+1}-{end_idx})')

plt.tight_layout()
plt.show()

## XGB 시각화 

In [ ]:
from xgboost import to_graphviz
import graphviz

to_graphviz(xgb_model)

## XGB 교차검증 

In [27]:
# 교차 검증
cv_results = xgb.cv(params=params, dtrain=dtrain, num_boost_round=10, nfold=3, metrics="mlogloss")
print(cv_results)

   train-mlogloss-mean  train-mlogloss-std  test-mlogloss-mean  \
0             1.088214            0.003226            1.097920   
1             0.897724            0.003055            0.914311   
2             0.783444            0.003711            0.806262   
3             0.708883            0.005186            0.736536   
4             0.656819            0.004341            0.688601   
5             0.619587            0.002191            0.653758   
6             0.590275            0.003268            0.627054   
7             0.566325            0.004498            0.606419   
8             0.547312            0.005729            0.590570   
9             0.526666            0.007163            0.573011   

   test-mlogloss-std  
0           0.001925  
1           0.003415  
2           0.004464  
3           0.002743  
4           0.002710  
5           0.004328  
6           0.003381  
7           0.005508  
8           0.007787  
9           0.011075  


In [29]:
import pickle

# 모델 학습
# xgb_model = xgboost.train(...)

# 모델 저장
with open('xgb_model.pkl', 'wb') as file:
    pickle.dump(xgb_model, file)